# Feature Extraction

In [1]:
%pip install orange3

,Requirement already satisfied: xlrd>=1.2.0 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (2.0.1)
,Requirement already satisfied: scikit-learn<1.2.0,>=1.0.1 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (1.1.3)
,Requirement already satisfied: httpx>=0.21.0 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (0.24.0)
,Requirement already satisfied: orange-widget-base>=4.19.0 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (4.20.0)
,Requirement already satisfied: numpy>=1.19.5 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (1.23.1)
,Requirement already satisfied: pandas!=1.5.0,>=1.3.0 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (2.0.1)
,Requirement already satisfied: xlsxwriter in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from orange3) (3.1.0)
,R

,Requirement already satisfied: importlib-metadata>=4.11.4 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from keyring->orange3) (6.6.0)
,Requirement already satisfied: jaraco.classes in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from keyring->orange3) (3.2.3)
,Requirement already satisfied: et-xmlfile in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from openpyxl->orange3) (1.1.0)
,Requirement already satisfied: charset-normalizer<3,>=2 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from requests->orange3) (2.1.0)
,Requirement already satisfied: urllib3<1.27,>=1.21.1 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from requests->orange3) (1.26.11)
,Requirement already satisfied: h11<0.15,>=0.13 in /Users/cuthbert/git/music21base/venv/lib/python3.10/site-packages (from httpcore<0.18.0,>=0.15.0->httpx>=0.21.0->orange3) (0.14.0)
,Requirement already satisfied: anyio<5.0,>=3.0 

In [2]:
from music21 import *

bach = corpus.parse('bach/bwv66.6')

In [3]:
blooming = corpus.parse('BloomingMeadowsJig')

In [4]:
reel = corpus.parse('7thRegimentReel')

In [5]:
ryanM = corpus.search('ryansMammoth')
ryanM

<music21.metadata.bundles.MetadataBundle {1059 entries}>

In [6]:
ryan = []
for i,metadata_entry in enumerate(ryanM):
    if i > 500:
        continue
    if 'jig' not in metadata_entry.corpusPath.lower() and i > 100:
        continue
    ryan.append(metadata_entry)

In [7]:
def is_jig(sc: stream.Score) -> bool:
    return 'jig' in sc.metadata.filePath.lower()

In [8]:
def write_ryan():
    my_path = '/Users/Cuthbert/Desktop'

    with open(f'{my_path}/train_data.tab', 'w') as training:
        with open(f'{my_path}/test_data.tab', 'w') as testing:
            columns = '\t'.join(['filename', 'numerator', 'denominator', 'eighths', 'sharps', 'is_jig'])
            training.write(columns + '\n')
            testing.write(columns + '\n')

            descriptions = '\t'.join(['string', 'discrete', 'discrete', 'continuous', 'discrete', 'discrete'])
            training.write(descriptions + '\n')
            testing.write(descriptions + '\n')

            meta_vars = '\t'.join(['meta', '' , '' , '', '', 'class'])
            training.write(meta_vars + '\n')
            testing.write(meta_vars + '\n')        

            for i, metadata_entry in enumerate(ryan):
                piece_parsed = metadata_entry.parse()
                features = feature_extractor(piece_parsed)
                features_str = '\t'.join([str(f) for f in features])
                if i % 2:
                    training.write(features_str + '\n')
                else:
                    testing.write(features_str + '\n')
        

## Using Music21 Features

In [9]:
from music21 import features


In [10]:
training_set = features.DataSet(classLabel='is_jig')
testing_set = features.DataSet(classLabel='is_jig')

In [11]:
fes = features.extractorsById(['ql1', 'ql2', 'ql3', 'm1', 'm2', 'm3', 'm4', 'm9', 'm15', 'p2', 'p8', 'p10', 'r15',])
fes

[music21.features.jSymbolic.MelodicIntervalHistogramFeature,
 music21.features.jSymbolic.AverageMelodicIntervalFeature,
 music21.features.jSymbolic.MostCommonMelodicIntervalFeature,
 music21.features.jSymbolic.DistanceBetweenMostCommonMelodicIntervalsFeature,
 music21.features.jSymbolic.RepeatedNotesFeature,
 music21.features.jSymbolic.MelodicOctavesFeature,
 music21.features.jSymbolic.NoteDensityFeature,
 music21.features.jSymbolic.MostCommonPitchClassPrevalenceFeature,
 music21.features.jSymbolic.PitchVarietyFeature,
 music21.features.jSymbolic.RangeFeature,
 music21.features.native.UniqueNoteQuarterLengths,
 music21.features.native.MostCommonNoteQuarterLength,
 music21.features.native.MostCommonNoteQuarterLengthPrevalence]

In [12]:
training_set.addFeatureExtractors(fes)
testing_set.addFeatureExtractors(fes)

# Start Your Coding here!